In [1]:
MAIN_PATH = "/home/carlos/MasterDS/tfm"
JSON_DATA_PATH = '{}/data/json/'.format(MAIN_PATH)
CSV_DATA_PATH = '{}/data/csv/'.format(MAIN_PATH)

In [2]:
import sys
sys.path.insert(0, MAIN_PATH)

In [3]:
%load_ext autoreload
%autoreload 2
from scripts.text.semantic_graph import SemanticGraph
from scripts.extractive_summary.key_events_graph import KeyEventsSummaryGraph

from scripts.conf import TEAMS

import pandas as pd

%reload_ext autoreload

# Extracción de eventos importantes usando grafos conceptuales

El objetivo de este experimento es utilizar los eventos de los partidos para crear un grafo conceptual, y extraer a partir de este los eventos 
más importantes (atendiendo al grado de los nodos, que serán palabras/entidades nombradas/sujetos nominales).

## Probando con eventos de un partido

In [5]:
key_events = KeyEventsSummaryGraph()

In [6]:
all_files = key_events.processor.load_json()

In [13]:
season_file = 'premier_league_2019_2020.json'
league_season_teams = TEAMS[season_file.split('.')[0]]
# Solo para pruebas
key_events.processor.league_season_teams = league_season_teams

In [8]:
match = all_files[season_file]['https://www.bbc.com/sport/football/49791610']

In [9]:
event_list = match['events']

In [10]:
event_list

['Foul by Matteo Guendouzi (Arsenal).',
 'Scott McTominay (Manchester United) wins a free kick in the defensive half.',
 'Granit Xhaka (Arsenal) wins a free kick in the defensive half.',
 'Foul by Jesse Lingard (Manchester United).',
 'Corner,  Arsenal. Conceded by Axel Tuanzebe.',
 'Hand ball by Bukayo Saka (Arsenal).',
 'Corner,  Manchester United. Conceded by Calum Chambers.',
 'Foul by Calum Chambers (Arsenal).',
 'Daniel James (Manchester United) wins a free kick on the left wing.',
 'Calum Chambers (Arsenal) is shown the yellow card for a bad foul.',
 'Offside, Manchester United. Ashley Young tries a through ball, but Harry Maguire is caught offside.',
 'Hand ball by Andreas Pereira (Manchester United).',
 'Offside, Arsenal. Bernd Leno tries a through ball, but Bukayo Saka is caught offside.',
 'Pierre-Emerick Aubameyang (Arsenal) wins a free kick on the left wing.',
 'Foul by Paul Pogba (Manchester United).',
 'Bukayo Saka (Arsenal) wins a free kick in the attacking half.',
 'Fo

In [9]:
semantic_graph = SemanticGraph(event_list)
g = semantic_graph.create_graph()

In [11]:
hubs_sentences = semantic_graph.get_n_hubs_sentences(n=10)

Hubs: [('Manchester United', 45), ('Arsenal', 40), ('attempt', 39), ('the box', 37), ('Bukayo Saka', 24), ('ball', 23), ('footed shot', 23), ('the centre', 23), ('Pierre-Emerick Aubameyang', 22), ('manchester united', 20)]


In [146]:
hubs_sentences

OrderedDict([('Manchester United',
              [(3,
                'Scott McTominay (Manchester United) wins a free kick in the defensive half.'),
               (5, 'Foul by Jesse Lingard (Manchester United).'),
               (8, 'Corner,  Manchester United. Conceded by Calum Chambers.'),
               (10,
                'Daniel James (Manchester United) wins a free kick on the left wing.'),
               (13, 'Hand ball by Andreas Pereira (Manchester United).'),
               (16, 'Foul by Paul Pogba (Manchester United).'),
               (18, 'Foul by Jesse Lingard (Manchester United).'),
               (20, 'Foul by Andreas Pereira (Manchester United).'),
               (22, 'Foul by Ashley Young (Manchester United).'),
               (24, 'Foul by Marcus Rashford (Manchester United).'),
               (25,
                'Marcus Rashford (Manchester United) is shown the yellow card for a bad foul.'),
               (27,
                'Axel Tuanzebe (Manchester United) 

In [11]:
count_vec_kwargs = {'ngram_range': (1, 2), 'strip_accents': 'unicode'}
n_hubs = 10
fc = 0.5
mode = 'homogeneous'

In [14]:
processed_events = key_events.process_match_events(event_list, n_hubs, fc, mode)

Hubs: [('manchester united', 50), ('arsenal', 39), ('attempt', 37), ('the box', 34), ('bukayo saka', 23), ('ball', 21), ('the centre', 21), ('pierre-emerick aubameyang', 20), ('footed shot', 20), ('andreas pereira', 19)]
Hubs with sentences: {'manchester united': 58, 'arsenal': 47, 'attempt': 24, 'the box': 20, 'bukayo saka': 12, 'ball': 8, 'the centre': 8, 'pierre-emerick aubameyang': 7, 'footed shot': 9, 'andreas pereira': 11}
The text has 119 events
The semantic graph has 65 nodes
The summary should have 60 sentences with a compression factor of 0.5
There are 112 sentences in the 10 nodes with more degree
Number of original events: 119
Number of processed events: 60


In [13]:
processed_events = key_events.process_match_events(event_list, n_hubs, fc, mode)

Hubs: [('bukayo saka', 5), ('pierre-emerick aubameyang', 4), ('joe willock', 4), ('scott mctominay', 3), ('ashley young', 2), ('nicolas pépé', 2), ('marcus rashford', 2), ('dani ceballos', 2), ('andreas pereira', 2), ('harry maguire', 1)]
Hubs with sentences: {'bukayo saka': 12, 'pierre-emerick aubameyang': 7, 'joe willock': 4, 'scott mctominay': 10, 'ashley young': 8, 'nicolas pépé': 2, 'marcus rashford': 6, 'dani ceballos': 4, 'andreas pereira': 2, 'harry maguire': 4}
The text has 119 events
The semantic graph has 17 nodes
The summary should have 60 sentences with a compression factor of 0.5
There are 47 sentences in the 10 nodes with more degree
Number of original events: 119
Number of processed events: 47


In [15]:
key_events.match_summary(match, count_vec_kwargs, save_relations=True, verbose=True, n_hubs=10, 
                         fc=fc, mode=mode)

Hubs: [('manchester united', 50), ('arsenal', 39), ('attempt', 37), ('the box', 34), ('bukayo saka', 23), ('ball', 21), ('the centre', 21), ('pierre-emerick aubameyang', 20), ('footed shot', 20), ('andreas pereira', 19)]
Hubs with sentences: {'manchester united': 58, 'arsenal': 47, 'attempt': 24, 'the box': 20, 'bukayo saka': 12, 'ball': 8, 'the centre': 8, 'pierre-emerick aubameyang': 7, 'footed shot': 9, 'andreas pereira': 11}
The text has 119 events
The semantic graph has 65 nodes
The summary should have 60 sentences with a compression factor of 0.5
There are 112 sentences in the 10 nodes with more degree
Number of original events: 119
Number of processed events: 60
Number of sentences in original article: 37
Number of sentences in summary: 10
Event:
Foul by Matteo Guendouzi (Arsenal).
Nearest sentence in article:
United had the edge on chances, although they were grateful to David de Gea for a fine double save from Saka and Matteo Guendouzi in the first half
Event:
Scott McTominay 

{'article_summary': 'In a disappointing encounter that was a pale shadow of their mighty clashes of years gone by, Scott McTominay gave Manchester United the lead at the end of an attritional first-half with a rising drive from the edge of the area.\nArsenal equalised just before the hour courtesy of Pierre-Emerick Aubameyang\'s cool finish.It was originally ruled out for offside but the video assistant referee confirmed the striker had been played onside by Harry Maguire.\nGoalkeeper Bernd Leno excelled for Arsenal with fine saves from Maguire and Marcus Rashford\'s late free-kick, while Bukayo Saka\'s goalbound shot crucially struck Victor Lindelof and flew over the top.\nMcTominay also headed a great chance well over from Ashley Young\'s corner but neither side could force a winner.\nManchester United\'s captain was 34-year-old Ashley Young, pressed into defensive service by Aaron Wan-Bissaka\'s absence through injury, and Arsenal were led by Granit Xhaka, newly appointed and a divi

### Con todos

In [4]:
summaries_path = '{}summaries/key_events_summaries_graph_5.csv'.format(CSV_DATA_PATH)
map_path = '{}summaries/key_events_summaries_graph_5_map.csv'.format(CSV_DATA_PATH)
count_vec_kwargs = {'ngram_range': (1, 2), 'strip_accents': 'unicode'}
n_hubs = 10
fc = 0.25
mode = 'homogeneous'

In [5]:
map_path

'/home/carlos/MasterDS/tfm/data/csv/summaries/key_events_summaries_graph_5_map.csv'

In [6]:
key_events = KeyEventsSummaryGraph(only_players=True)

In [7]:
%%time
pd_df = key_events.run(save_events_sentences=True, path_csv=summaries_path, 
                       path_mapping=map_path, count_vec_kwargs=count_vec_kwargs,
                       n_hubs=n_hubs, fc=fc, mode=mode
                       )

  0%|          | 0/20 [00:00<?, ?it/s]

Hubs: [('sergio agüero', 5), ('riyad mahrez', 5), ('ilkay gündogan', 3), ('anthony knockaert', 3), ('glenn murray', 3), ('david silva', 3), ('bernardo silva', 2), ('raheem sterling', 2), ('kyle walker', 2), ('pascal groß', 2)]
Hubs with sentences: {'sergio agüero': 9, 'riyad mahrez': 8, 'ilkay gündogan': 7, 'anthony knockaert': 9, 'glenn murray': 5, 'david silva': 7, 'bernardo silva': 3, 'raheem sterling': 6, 'kyle walker': 6, 'pascal groß': 3}
The text has 83 events
The semantic graph has 20 nodes
The summary should have 21 sentences with a compression factor of 0.25
There are 50 sentences in the 10 nodes with more degree
Number of original events: 83
Number of processed events: 21
Number of sentences in original article: 6
Number of sentences in summary: 3
Hubs: [('chris wood', 6), ('ashley barnes', 5), ('alex iwobi', 4), ('joe willock', 3), ('dwight mcneil', 3), ('johann gudmundsson', 3), ('charlie taylor', 2), ('pierre-emerick aubameyang', 2), ('matthew lowton', 2), ('ashley westwo

  5%|▌         | 1/20 [16:50<5:20:00, 1010.53s/it]

Number of sentences in original article: 6
Number of sentences in summary: 3
Hubs: [('cristhian lagos', 3), ('jonatan hansen', 2), ('darwin quintero', 1), ('michael arroyo', 1), ('keyner brown', 1), ('luis omar hernández', 1), ('paolo goltz', 1), ('paul aguilar', 1), ('esteban ramirez', 1), ('nelson', 1)]
Hubs with sentences: {'cristhian lagos': 4, 'jonatan hansen': 4, 'darwin quintero': 5, 'michael arroyo': 3, 'keyner brown': 8, 'luis omar hernández': 5, 'paolo goltz': 2, 'paul aguilar': 6, 'esteban ramirez': 3, 'nelson': 1}
The text has 118 events
The semantic graph has 11 nodes
The summary should have 30 sentences with a compression factor of 0.25
There are 35 sentences in the 10 nodes with more degree
Number of original events: 118
Number of processed events: 30
Number of sentences in original article: 14
Number of sentences in summary: 7
Hubs: [('david villa', 4), ('bradley wright-phillips', 3), ('andrew jacobson', 2), ('thomas mcnamara', 2), ('chris duvall', 2), ('dax mccarty', 2

/home/carlos/MasterDS/tfm/scripts/extractive_summary/key_events_graph.py:154: UserWarning: Required hubs are higher than available nodes. Using 0 hubs
  warnings.warn('Required hubs are higher than available nodes. Using {} hubs'.format(n_nodes))
/home/carlos/MasterDS/tfm/scripts/text/semantic_graph.py:214: UserWarning: Graph could not be created. Returning empty list
  warnings.warn("Graph could not be created. Returning empty list")
/home/carlos/MasterDS/tfm/scripts/text/semantic_graph.py:229: UserWarning: Could not create hubs out of graph. Returning empty dict
  warnings.warn("Could not create hubs out of graph. Returning empty dict")
/home/carlos/MasterDS/tfm/scripts/extractive_summary/key_events_graph.py:161: UserWarning: Hubs sentences is empty. Returning empty list
  warnings.warn("Hubs sentences is empty. Returning empty list")
/home/carlos/MasterDS/tfm/scripts/extractive_summary/key_events.py:40: UserWarning: Could not perform tfidf
  warnings.warn('Could not perform tfidf')


...

/home/carlos/MasterDS/tfm/scripts/extractive_summary/key_events.py:50: UserWarning: Could not perform tfidf
  warnings.warn('Could not perform tfidf')
/home/carlos/MasterDS/tfm/scripts/extractive_summary/key_events_graph.py:245: UserWarning: Could not perform summary for https://www.bbc.com/sport/football/49899766
  warnings.warn('Could not perform summary for {}'.format(match_url))
 95%|█████████▌| 19/20 [3:24:52<04:15, 255.22s/it]

Hubs: [('marco parolo', 6), ('sergej milinkovic-savic', 5), ('senad lulic', 4), ('immobile', 3), ('francesco acerbi', 3), ('felipe caicedo', 3), ('danilo cataldi', 3), ('fabio quagliarella', 2), ('ciro immobile', 2), ('stefan radu', 2)]
Hubs with sentences: {'marco parolo': 7, 'sergej milinkovic-savic': 13, 'senad lulic': 13, 'immobile': 4, 'francesco acerbi': 3, 'felipe caicedo': 4, 'danilo cataldi': 3, 'fabio quagliarella': 4, 'ciro immobile': 4, 'stefan radu': 5}
The text has 129 events
The semantic graph has 19 nodes
The summary should have 32 sentences with a compression factor of 0.25
There are 43 sentences in the 10 nodes with more degree
Number of original events: 129
Number of processed events: 32
Number of sentences in original article: 8
Number of sentences in summary: 4
Hubs: [('paulo dybala', 6), ('cristiano ronaldo', 4), ('joão mário', 3), ('leonardo bonucci', 3), ('mario mandzukic', 3), ('rodrigo bentancur', 3), ('lautaro martínez', 3), ('ivan perisic', 2), ('joão cancel

100%|██████████| 20/20 [3:28:29<00:00, 625.50s/it]

Number of sentences in original article: 8
Number of sentences in summary: 5


Saving summaries in /home/carlos/MasterDS/tfm/data/csv/summaries/key_events_summaries_graph_5.csv
Saving mappings in /home/carlos/MasterDS/tfm/data/csv/summaries/key_events_summaries_graph_5_map.csv
CPU times: user 3h 27min 32s, sys: 1min 9s, total: 3h 28min 42s
Wall time: 3h 28min 34s


In [8]:
pd_df['summary_events'].values[0]

'Corner,  Brighton and Hove Albion. Conceded by Aymeric Laporte. Offside, Brighton and Hove Albion. Anthony Knockaert tries a through ball, but Glenn Murray is caught offside. Foul by Anthony Knockaert (Brighton and Hove Albion). Attempt missed. Alireza Jahanbakhsh (Brighton and Hove Albion) right footed shot from outside the box is close, but misses to the left. Assisted by Anthony Knockaert following a fast break. Foul by Yves Bissouma (Brighton and Hove Albion). Foul by Glenn Murray (Brighton and Hove Albion). Glenn Murray (Brighton and Hove Albion) wins a free kick in the defensive half. Attempt blocked. Alireza Jahanbakhsh (Brighton and Hove Albion) right footed shot from outside the box is blocked. Corner,  Brighton and Hove Albion. Conceded by Raheem Sterling. Goal.  Brighton and Hove Albion 1, Manchester City 0. Glenn Murray (Brighton and Hove Albion) header from the left side of the six yard box to the bottom left corner. Assisted by Pascal Groß with a cross following a corner

## Resultados

__Resúmenes__

In [7]:
pd_df_sum = pd.read_csv(summaries_path)

In [8]:
pd_df_sum

json_file  \
0     italian_serie_a_2019_2020.json   
1     italian_serie_a_2019_2020.json   
2     italian_serie_a_2019_2020.json   
3     italian_serie_a_2019_2020.json   
4     italian_serie_a_2019_2020.json   
...                              ...   
4371              mls_2019_2020.json   
4372              mls_2019_2020.json   
4373              mls_2019_2020.json   
4374              mls_2019_2020.json   
4375              mls_2019_2020.json   

                                                    url  \
0           https://www.bbc.com/sport/football/49871134   
1           https://www.bbc.com/sport/football/49873763   
2           https://www.bbc.com/sport/football/49865134   
3           https://www.bbc.com/sport/football/49866723   
4           https://www.bbc.com/sport/football/49832309   
...                                                 ...   
4371  https://matchcenter.mlssoccer.com/matchcenter/...   
4372  https://matchcenter.mlssoccer.com/matchcenter/...   
4373  https://matchcenter.mlssoccer.com/matchcenter/...   
4374  https://matchcenter.mlssoccer.com/matchcenter/...   
4375  https://matchcenter.mlssoccer.com/matchcenter/...   

                                                summary  \
0     Mario Balotelli scored his first Serie A goal ...   
1     Fiorentina condemned AC Milan to a third conse...   
2     Cristiano Ronaldo returned from injury with a ...   
3     Alexis Sanchez scored and was sent off on his ...   
4     On-loan Manchester United defender Chris Small...   
...                                                 ...   
4371  After lacking the final product for much of 11...   
4372  Jamiro Monteiro scored his second MLS goal on ...   
4373  Nelson Bonilla's goal in first-half stoppage t...   
4374  Alphonso Davies quick-kicked the ball to Jonat...   
4375  The Colorado Rapids are on a roll.The Rapids' ...   

                                      article_sentences  \
0     ['Mario Balotelli scored his first Serie A goa...   
1     ['Fiorentina condemned AC Milan to a third con...   
2     ['Cristiano Ronaldo returned from injury with ...   
3     ['Alexis Sanchez scored and was sent off on hi...   
4     ['On-loan Manchester United defender Chris Sma...   
...                                                 ...   
4371  ['After lacking the final product for much of ...   
4372  ['Jamiro Monteiro scored his second MLS goal\x...   
4373  ["Nelson Bonilla's goal in first-half stoppage...   
4374  ["Haiti came back from a two-goal halftime def...   
4375  ['The\xa0Colorado Rapids\xa0are on a roll.', "...   

                                   article_sentences_ix  \
0     [ 0 10  0  2  1  6  6  6  6  6  1  1  6  0  2 ...   
1     [0 3 2 5 2 2 0 0 2 2 2 1 1 1 3 0 2 5 1 1 1 5 5...   
2     [0 0 0 0 3 0 3 1 2 0 0 3 3 3 0 0 3 0 0 0 0 0 2...   
3     [4 0 0 1 1 0 1 0 0 1 0 0 1 0 3 0 0 4 0 0 1 1 1...   
4     [4 4 4 4 4 3 4 4 2 4 4 3 3 0 4 3 4 4 4 4 4 4 4...   
...                                                 ...   
4371  [1 1 4 1 1 3 1 3 3 8 0 3 1 3 1 1 8 1 2 1 1 1 1...   
4372  [1 1 4 3 3 3 3 3 3 3 3 3 3 3 3 3 3 0 3 3 3 1 1...   
4373  [ 6  0  6  6 20  6  7  7  0  6 20  9  6  8  0 ...   
4374  [ 9  9 10  8  3 10  9  4  3  9  6  3  3  3  6 ...   
4375  [0 2 2 0 0 0 0 0 2 2 0 5 0 2 0 2 0 0 0 5 2 5 2...   

                                         events_mapping  
0     [2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 15, 16, 1...  
1     [2, 3, 4, 5, 6, 8, 9, 10, 11, 12, 13, 15, 16, ...  
2     [5, 6, 7, 8, 11, 15, 16, 17, 19, 21, 23, 26, 2...  
3     [3, 4, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 18,...  
4     [2, 4, 9, 12, 14, 15, 16, 17, 18, 20, 21, 22, ...  
...                                                 ...  
4371  [2, 4, 5, 8, 9, 10, 11, 12, 13, 14, 15, 17, 18...  
4372  [2, 5, 7, 9, 10, 11, 13, 14, 16, 17, 22, 23, 2...  
4373  [2, 4, 6, 9, 12, 13, 14, 16, 17, 18, 19, 21, 2...  
4374  [2, 3, 6, 9, 11, 12, 13, 14, 15, 16, 17, 18, 1...  
4375  [3, 4, 6, 7, 8, 10, 12, 13, 15, 17, 19, 23, 25...  

[4376 rows x 

__Relación evento-frase__

In [9]:
pd_df_map = pd.read_csv(map_path)

In [10]:
pd_df_map

event  \
0       Attempt blocked. Mario Balotelli (Brescia) rig...   
1           Corner,  Napoli. Conceded by Stefano Sabelli.   
2       Attempt missed. Mario Balotelli (Brescia) left...   
3       Attempt saved. Mario Balotelli (Brescia) right...   
4       Goal!  Napoli 1, Brescia 0. Dries Mertens (Nap...   
...                                                   ...   
111401  Attempt saved. Rodolfo Zelaya (Los Angeles Foo...   
111402  Attempt blocked. Keegan Rosenberry (Colorado R...   
111403  Attempt missed. Rodolfo Zelaya (Los Angeles Fo...   
111404  Attempt blocked. Mohamed El-Munir (Los Angeles...   
111405  Attempt saved. Diego Rossi (Los Angeles Footba...   

                                         article_sentence  
0       Mario Balotelli scored his first Serie A goal ...  
1       Watford striker Stefano Okaka scored the winne...  
2       Mario Balotelli scored his first Serie A goal ...  
3       Brescia rallied after the break but Sandro Ton...  
4       Dries Mertens opened the scoring with his four...  
...                                                   ...  
111401  The Rapids' lone goal came on a corner kick, a...  
111402                 The Colorado Rapids are on a roll.  
111403  The Rapids' lone goal came on a corner kick, a...  
111404                 The Colorado Rapids are on a roll.  
111405  The Rapids' lone goal came on a corner kick, a...  

[111406 rows x 2 columns]

In [71]:
pd_df_map.iloc[89985]['event']

'Goal!  Real Sociedad 1, Barcelona 0. Aritz Elustondo (Real Sociedad) left footed shot from the left side of the box to the bottom left corner following a set piece situation.'

In [72]:
pd_df_map.iloc[89985]['article_sentence']

'The champions fell behind following a thumping shot from Aritz Elustondo in the 12th minute from a set piece.'

In [37]:
pd_df_goal = pd_df_map[pd_df_map['event'].str.contains('goal') &
                       ~pd_df_map['event'].str.contains('attempt') &
                       ~pd_df_map['event'].str.contains('Attempt')]  

In [35]:
len(pd_df_goal)

1044

In [44]:
pd_df_goal.iloc[600]['event']

'Goal!  Watford 0, Chelsea 2. Christian Pulisic (Chelsea) right footed shot from very close range to the centre of the goal. Assisted by Tammy Abraham.'

In [45]:
pd_df_goal.iloc[600]['article_sentence']

"In blustery conditions, the visitors opened the scoring after five minutes when Jorginho's delicious pass allowed Tammy Abraham to lift in his 10th goal of the season.\n"

In [47]:
pd_df_goal.iloc[601]['event']

'Goal!  Newcastle United 1, Wolverhampton Wanderers 0. Jamaal Lascelles (Newcastle United) header from very close range to the high centre of the goal. Assisted by Federico Fernández with a cross.'

In [48]:
pd_df_goal.iloc[601]['article_sentence']

"Magpies captain Jamaal Lascelles scored the opener with a powerful near-post header from Federico Fernandez's cross to light up what had been a largely dour first half.\n"